<a href="https://colab.research.google.com/github/luanfelixcoding/climate-change-impact-economy/blob/master/climate_change_impact_economy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Link para base de dados:** https://www.kaggle.com/datasets/tarunrm09/climate-change-indicators

**Link para base de dados:** https://www.kaggle.com/datasets/sazidthe1/global-inflation-data?resource=download

**Link para base de dados:** https://www.kaggle.com/datasets/samithsachidanandan/average-monthly-surface-temperature-1940-2024

In [124]:
# conectando com o drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## Importando Bibliotecas

In [125]:
# importando bibliotecas
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression

## Data Loading

In [126]:
climate_change_file_path: str = "/content/drive/My Drive/datasets/climate_change_dataset/climate_change_indicators.csv"
global_inflation_file_path : str = "/content/drive/My Drive/datasets/global_inflation_dataset/global_inflation_data.csv"
surface_temperature_file_path : str = "/content/drive/My Drive/datasets/surface_temperature_dataset/average-monthly-surface-temperature.csv"

# datasets
df_climate = pd.read_csv(climate_change_file_path)
df_economy = pd.read_csv(global_inflation_file_path)
df_surface_temperature = pd.read_csv(surface_temperature_file_path)

df_climate.info(), df_economy.info(), df_surface_temperature.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 225 entries, 0 to 224
Data columns (total 72 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ObjectId             225 non-null    int64  
 1   Country              225 non-null    object 
 2   ISO2                 223 non-null    object 
 3   ISO3                 225 non-null    object 
 4   Indicator            225 non-null    object 
 5   Unit                 225 non-null    object 
 6   Source               225 non-null    object 
 7   CTS_Code             225 non-null    object 
 8   CTS_Name             225 non-null    object 
 9   CTS_Full_Descriptor  225 non-null    object 
 10  F1961                188 non-null    float64
 11  F1962                189 non-null    float64
 12  F1963                188 non-null    float64
 13  F1964                188 non-null    float64
 14  F1965                188 non-null    float64
 15  F1966                192 non-null    flo

(None, None, None)

## Data exploration | Data cleaning | Data Wrangling

In [127]:
# verificando valores nulos em cada coluna
def checking_null_values(df: pd.DataFrame) -> None:
  for col in df.columns:
    if df[col].isnull().sum() > 0:
      print(f"{df[col].name} = {df[col].isnull().sum()}")

### Dataset Surface_Temperature

In [128]:
# Filtrar apenas os anos de 1960 em diante
# df_surface_temperature = df_surface_temperature[(df_surface_temperature['year'] >= 1960) & (df_surface_temperature['year'] <= 2022)]

# Aplicando o melt() para organizar os dados
df_surface_temperature_melted = df_surface_temperature.melt(
    id_vars=['Entity', 'Code', 'year'],  # Mantemos essas colunas fixas
    value_vars=['Average surface temperature'],  # Transformamos essa coluna em linhas
    var_name='Temperature_Type',  # Nome da nova coluna indicando o tipo de dado
    value_name='Temperature'  # Nome dos valores de temperatura
)

df_surface_temperature_melted.dropna(subset=['Temperature'], inplace=True)

global_temp_trend_1 = df_surface_temperature_melted.groupby('year', as_index=False)['Temperature'].mean().sort_values(by='year')
global_temp_trend_1

year  Temperature
0   1940    17.241399
1   1941    17.555396
2   1942    17.397509
3   1943    17.471349
4   1944    17.611624
..   ...          ...
80  2020    19.114152
81  2021    18.953754
82  2022    18.981230
83  2023    19.395925
84  2024    19.594957

[85 rows x 2 columns]

### Dataset Climate_Change

In [129]:
# Pegando apenas as colunas que representam anos no df_climate
years = [col for col in df_climate.columns if col.startswith('F')]

# Derrete o dataset em variaveis e valores
# 'Country' e 'ISO3' mantemos, nomeamos uma coluna como 'Year' que recebe a variavel 'years'
df_climate_melted = df_climate.melt(
    id_vars=['Country', 'ISO3'],
    value_vars=years,
    var_name='Year',
    value_name='Temperature_Change'
)

# Na coluna 'Year' extraindo todos os numeros e convertendo para int, "(\d+)" permite extrair numeros compostos
df_climate_melted['Year'] = df_climate_melted['Year'].str.extract("(\d+)").astype(int)
df_climate_melted.rename(columns={'Country': 'country_name'}, inplace=True)
# checking_null_values(df_climate_melted) # output: Temperature_Change = 1490

# Removendo valores nulos; inplace=True faz as alterações no proprio df, inplace=False cria outro df com os valores removidos
df_climate_melted.dropna(subset=['Temperature_Change'], inplace=True)

# checking_null_values(df_climate_melted) # output: Temperature_Change = 0

# Agrupando a coluna 'Year' e pegando a media de seus valores em conjunto
global_temp_trend_2 = df_climate_melted.groupby('Year', as_index=False)['Temperature_Change'].mean().sort_values(by='Year')
display(df_climate_melted.head())
display(global_temp_trend_2.head())

country_name ISO3  Year  Temperature_Change
0  Afghanistan, Islamic Rep. of  AFG  1961              -0.113
1                       Albania  ALB  1961               0.627
2                       Algeria  DZA  1961               0.164
3                American Samoa  ASM  1961               0.079
4      Andorra, Principality of  AND  1961               0.736

Year  Temperature_Change
0  1961            0.163053
1  1962           -0.013476
2  1963           -0.006043
3  1964           -0.070059
4  1965           -0.247027

## Data Analysis and Visualization

In [130]:
fig_global = go.Figure()

fig_global.add_trace(
    go.Scatter(
        x=global_temp_trend_1['year'],
        y=global_temp_trend_1['Temperature'],
        mode='lines+markers',
        line=dict(color='blue', width=2),
        marker=dict(color='black', size=5),
        name='Tendência Global'
    )
)

fig_global.update_layout(
    title='Tendência Global da Mudança de Temperatura (1940-2024)',
    xaxis_title='year',
    yaxis_title='Temperatura Média da Superfície (°C)',
    template='plotly_white',
    showlegend=True,
)

fig_global.show()

In [131]:
fig_global = go.Figure()

fig_global.add_trace(go.Scatter(
    x=global_temp_trend_2['Year'],
    y=global_temp_trend_2['Temperature_Change'],
    mode='lines+markers',
    line=dict(color='red', width=2),  # Linha vermelha
    marker=dict(color='black', size=5),  # Pontos pretos
    name='Tendência Global'
))


fig_global.update_layout(
    title="Tendência Global da Mudança de Temperatura (1961-2022)",
    xaxis_title="Ano",
    yaxis_title="Mudança Média de Temperatura (°C)",
    template="plotly_white",
    showlegend=True
)

# Exibir o gráfico
fig_global.show()

In [132]:
# Filtra apenas os anos de 1961 em diante para o primeiro conjunto de dados
df_surface_temperature = df_surface_temperature[df_surface_temperature['year'] >= 1961]

# Agrupa os anos e calcular a média das temperaturas (primeiro conjunto de dados)
global_temp_trend_1 = df_surface_temperature.groupby('year', as_index=False)['Average surface temperature'].mean()

# Agrupa os anos e calcular a média das mudanças de temperatura (segundo conjunto de dados)
global_temp_trend_2 = df_climate_melted.groupby('Year', as_index=False)['Temperature_Change'].mean().sort_values(by='Year')

fig = go.Figure()

# Adicionar a primeira linha (Temperatura média da superfície)
fig.add_trace(go.Scatter(
    x=global_temp_trend_1['year'],
    y=global_temp_trend_1['Average surface temperature'],
    mode='lines+markers',
    line=dict(color='red', width=2),
    marker=dict(color='black', size=5),
    name='Temperatura Média da Superfície'
))

# Adicionar a segunda linha (Mudança média de temperatura)
fig.add_trace(go.Scatter(
    x=global_temp_trend_2['Year'],
    y=global_temp_trend_2['Temperature_Change'],
    mode='lines+markers',
    line=dict(color='blue', width=2),
    marker=dict(color='black', size=5),
    name='Mudança Média de Temperatura'
))

# Atualizar o layout
fig.update_layout(
    title='Comparação da Temperatura Média da Superfície e Mudança Média de Temperatura (1960-2024)',
    xaxis_title='Ano',
    yaxis_title='Temperatura (°C)',
    template='plotly_white',
    showlegend=True
)

# Mostrar o gráfico
fig.show()


In [133]:
# Calcula a média anual de temperatura por país
df_avg_temp_per_year = df_surface_temperature_melted.groupby(["Entity", "year"])["Temperature"].mean().reset_index()

# Calcula a diferença anual de temperatura (variação em relação ao ano anterior)
df_avg_temp_per_year['Temperature_Change'] = df_avg_temp_per_year.groupby("Entity")["Temperature"].diff()

# Seleciona os 10 países com maior variação total de temperatura
df_temperature_variation = df_avg_temp_per_year.groupby("Entity")["Temperature_Change"].agg(lambda x: x.abs().sum())
top_10_countries = df_temperature_variation.nlargest(10).index

# Filtra apenas os 10 países mais afetados e ordenar os dados
df_top_10_countries = df_avg_temp_per_year[df_avg_temp_per_year['Entity'].isin(top_10_countries)].sort_values(by=['year'])

# Cria o gráfico interativo mostrando a variação da temperatura ano a ano
fig_countries = px.line(df_top_10_countries, x="year", y="Temperature_Change", color="Entity",
                        title="Variação Anual da Temperatura nos 10 Países com Maior Mudança",
                        labels={"Temperature_Change": "Variação da Temperatura Média Anual (°C)", "year": "Ano"},
                        markers=True)

fig_countries.update_traces(line=dict(width=2))
fig_countries.show()


In [134]:
# Calculando a variação de temperatura por país (máximo - mínimo)
df_climate_variation = df_climate_melted.groupby("country_name")["Temperature_Change"].agg(lambda x: x.max() - x.min())

# Selecionando os 10 países mais afetados (com maior variação)
top_10_countries = df_climate_variation.nlargest(10).index
df_top_10_countries = df_climate_melted[df_climate_melted['country_name'].isin(top_10_countries)].sort_values(by=['Year'])

# Criando o gráfico interativo
fig_countries = px.line(df_top_10_countries, x="Year", y="Temperature_Change", color="country_name",
                        title="Comparação dos Países com Maior Variação ao longo dos Anos",
                        labels={"Temperature_Change": "Mudança Média de Temperatura (°C)", "Year": "Ano"},
                        markers=True)

fig_countries.update_traces(line=dict(width=2))
fig_countries.show()


# Dados sobre o dataset de Economia

In [135]:
df_economy_melted = df_economy.melt(
    id_vars=['country_name'],
    value_vars=[str(col) for col in range(1980, 2025)],
    var_name='Year',
    value_name='Inflation'
)
df_economy_melted['Year'] = df_economy_melted['Year'].astype(int)


# Combina e limpa dados
df_combined = pd.merge(df_climate_melted, df_economy_melted, on=['country_name', 'Year'], how='inner').dropna()

# Calcula correlacao
correlation = df_combined[['Temperature_Change', 'Inflation']].corr().iloc[0, 1]

In [136]:
# Create scatter plot with trendline
fig = px.scatter(
    df_combined,
    x='Temperature_Change',
    y='Inflation',
    opacity=0.5,
    title=f'Correlação entre Mudança de Temperatura e Inflação: {correlation:.2f}',
    labels={'Temperature_Change': 'Mudança Média de Temperatura (°C)', 'Inflation': 'Inflação (%)'},
    template='plotly_white',
    trendline='ols',
    width=800,
    height=500
)

# Add grid and show plot
fig.update_xaxes(showgrid=True, gridcolor='lightgray')
fig.update_yaxes(showgrid=True, gridcolor='lightgray')
fig.show()

In [137]:
# Análise de Volatilidade Econômica
top_volatility = df_economy_melted.groupby('country_name')['Inflation'].std().nlargest(10).reset_index()

# Gráfico de barras com Plotly
fig = px.bar(
    top_volatility,
    y='country_name',
    x='Inflation',
    orientation='h',
    color='Inflation',
    color_continuous_scale='Viridis',
    title="Top 10 Países com Maior Volatilidade Econômica (Inflação)",
    labels={'Inflation': 'Desvio Padrão da Inflação (%)', 'country_name': 'País'},
    width=800,
    height=500
)

# Ajustes visuais
fig.update_xaxes(showgrid=True, gridcolor='lightgray', zeroline=True, zerolinecolor='gray')
fig.show()

In [138]:
df_combined = pd.merge(df_climate_melted, df_economy_melted, on=['country_name', 'Year'], how='inner')
df_combined_clean = df_combined.dropna()
df_combined_clean.head()

country_name ISO3  Year  Temperature_Change  Inflation
1              Algeria  DZA  1980               0.232        9.7
2               Angola  AGO  1980               0.279       46.7
3  Antigua and Barbuda  ATG  1980               0.646       19.0
5            Australia  AUS  1980               0.887       10.1
6              Austria  AUT  1980              -0.274        6.3

In [139]:
# Agrupar a inflação por ano e calcular a média global
df_economy_avg = df_economy_melted.groupby('Year', as_index=False)['Inflation'].mean()

# Juntar os dados de temperatura e inflação pelo ano
df_merged = pd.merge(global_temp_trend_2, df_economy_avg, left_on='Year', right_on='Year')

# Criar um gráfico de dispersão para visualizar a relação
fig = px.scatter(df_merged, x="Temperature_Change", y="Inflation",
                 title="Relação entre Mudança de Temperatura e Inflação Global",
                 labels={"Temperature_Change": "Mudança de Temperatura Média (°C)", "Inflation": "Inflação (%)"},
                 trendline="ols")  # Adiciona uma linha de regressão

fig.show()

In [141]:
# Definindo as variáveis de entrada (ano) e saída (temperatura)
X = df_surface_temperature_melted['year'].values.reshape(-1, 1)
y = df_surface_temperature_melted['Temperature'].values

# Inicializando o modelo de regressão linear
model = LinearRegression()

# Ajustando o modelo aos dados
model.fit(X, y)

# Fazendo a previsão para os anos do dataset
df_surface_temperature_melted['Predicted_Temperature'] = model.predict(X)

# Prevendo a temperatura para os próximos anos (exemplo: até 2030)
future_years = np.arange(2023, 2031).reshape(-1, 1)
future_predictions = model.predict(future_years)

# Criando o gráfico interativo com Plotly
fig = go.Figure()

# Adicionando os pontos de dados reais
fig.add_trace(go.Scatter(x=df_surface_temperature_melted['year'],
                         y=df_surface_temperature_melted['Temperature'],
                         mode='markers',
                         marker=dict(color='blue'),
                         name='Dados Reais'))

# Adicionando a linha de tendência da regressão linear
fig.add_trace(go.Scatter(x=df_surface_temperature_melted['year'],
                         y=df_surface_temperature_melted['Predicted_Temperature'],
                         mode='lines',
                         line=dict(color='red'),
                         name='Tendência (Regressão Linear)'))

# Adicionando previsões futuras
fig.add_trace(go.Scatter(x=future_years.flatten(),
                         y=future_predictions,
                         mode='lines',
                         line=dict(color='green', dash='dash'),
                         name='Previsões Futuras'))

# Personalizando layout do gráfico
fig.update_layout(title='Tendência Global da Temperatura com Previsão Futura',
                  xaxis_title='Ano',
                  yaxis_title='Temperatura (°C)',
                  legend_title='Legenda',
                  template='plotly_white')

# Exibindo o gráfico
fig.show()

# Exibindo as previsões para os próximos anos
future_years_df = pd.DataFrame({'year': future_years.flatten(), 'Predicted_Temperature': future_predictions})
print(future_years_df)

   year  Predicted_Temperature
0  2023              18.906163
1  2024              18.926507
2  2025              18.946850
3  2026              18.967194
4  2027              18.987538
5  2028              19.007882
6  2029              19.028225
7  2030              19.048569
